In [1]:
# data science libraries
import pandas as pd
import cv2
import numpy as np
import matplotlib.pyplot as plt
np.random.seed(1000)

# keras and tf
import tensorflow as tf
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Dense, Dropout, Flatten, Conv2D, MaxPool2D, Input
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras import optimizers

# other tf imports
from tensorflow.keras.preprocessing.image import ImageDataGenerator

# print validation statement
print("all resources loaded")

all resources loaded


In [2]:
df = pd.read_csv('data/HAM10000_metadata.csv')
df.head()

lesion_id      image_id   dx dx_type   age   sex localization
0  HAM_0000118  ISIC_0027419  bkl   histo  80.0  male        scalp
1  HAM_0000118  ISIC_0025030  bkl   histo  80.0  male        scalp
2  HAM_0002730  ISIC_0026769  bkl   histo  80.0  male        scalp
3  HAM_0002730  ISIC_0025661  bkl   histo  80.0  male        scalp
4  HAM_0001466  ISIC_0031633  bkl   histo  75.0  male          ear

In [3]:
df['image_id'] = df['image_id'].apply(lambda x: '{}.jpg'.format(x))
df.head()

lesion_id          image_id   dx dx_type   age   sex localization
0  HAM_0000118  ISIC_0027419.jpg  bkl   histo  80.0  male        scalp
1  HAM_0000118  ISIC_0025030.jpg  bkl   histo  80.0  male        scalp
2  HAM_0002730  ISIC_0026769.jpg  bkl   histo  80.0  male        scalp
3  HAM_0002730  ISIC_0025661.jpg  bkl   histo  80.0  male        scalp
4  HAM_0001466  ISIC_0031633.jpg  bkl   histo  75.0  male          ear

In [4]:
df['image_id'] = df['image_id'].apply(lambda x: 'data/HAM10000_images/{}'.format(x))
df.head()

lesion_id                               image_id   dx dx_type   age  \
0  HAM_0000118  data/HAM10000_images/ISIC_0027419.jpg  bkl   histo  80.0   
1  HAM_0000118  data/HAM10000_images/ISIC_0025030.jpg  bkl   histo  80.0   
2  HAM_0002730  data/HAM10000_images/ISIC_0026769.jpg  bkl   histo  80.0   
3  HAM_0002730  data/HAM10000_images/ISIC_0025661.jpg  bkl   histo  80.0   
4  HAM_0001466  data/HAM10000_images/ISIC_0031633.jpg  bkl   histo  75.0   

    sex localization  
0  male        scalp  
1  male        scalp  
2  male        scalp  
3  male        scalp  
4  male          ear

In [5]:
def numerizing(x):
    dict = {
        'nv': 0,
        'mel': 1,
        'bkl': 2,
        'bcc': 3,
        'akiec': 4,
        'vasc': 5,
        'df': 6
    }
    return dict[x]

df['dx_num'] = df['dx'].apply(lambda x: numerizing(x))
df.head()

lesion_id                               image_id   dx dx_type   age  \
0  HAM_0000118  data/HAM10000_images/ISIC_0027419.jpg  bkl   histo  80.0   
1  HAM_0000118  data/HAM10000_images/ISIC_0025030.jpg  bkl   histo  80.0   
2  HAM_0002730  data/HAM10000_images/ISIC_0026769.jpg  bkl   histo  80.0   
3  HAM_0002730  data/HAM10000_images/ISIC_0025661.jpg  bkl   histo  80.0   
4  HAM_0001466  data/HAM10000_images/ISIC_0031633.jpg  bkl   histo  75.0   

    sex localization  dx_num  
0  male        scalp       2  
1  male        scalp       2  
2  male        scalp       2  
3  male        scalp       2  
4  male          ear       2

In [6]:
df['dx'].value_counts().to_dict()

{'nv': 6705,
 'mel': 1113,
 'bkl': 1099,
 'bcc': 514,
 'akiec': 327,
 'vasc': 142,
 'df': 115}

In [7]:
df['dx_num'].value_counts().to_dict()

{0: 6705, 1: 1113, 2: 1099, 3: 514, 4: 327, 5: 142, 6: 115}

In [8]:
class_labels = ['nv', 'mel', 'bkl', 'bcc', 'akiec', 'vasc', 'df']
n_classes = 7

w = {}
vc = df['dx'].value_counts().items()
w_sum = 0
for lab, val in vc:
    w[str(lab)] = val
    w_sum += val

class_weight = {
    0: 0,
    1: 0,
    2: 0,
    3: 0,
    4: 0,
    5: 0,
    6: 0
}

ind = 0
for i in w:
    class_weight[ind] = w_sum / (n_classes * w[i])
    ind += 1

class_weight

{0: 0.21338020666879728,
 1: 1.2854575792581184,
 2: 1.301832835044846,
 3: 2.78349082823791,
 4: 4.375273044997815,
 5: 10.075452716297788,
 6: 12.440993788819876}

In [9]:
cw = [val for lab, val in class_weight.items()]
cw

[0.21338020666879728,
 1.2854575792581184,
 1.301832835044846,
 2.78349082823791,
 4.375273044997815,
 10.075452716297788,
 12.440993788819876]

In [10]:
df.head()

lesion_id                               image_id   dx dx_type   age  \
0  HAM_0000118  data/HAM10000_images/ISIC_0027419.jpg  bkl   histo  80.0   
1  HAM_0000118  data/HAM10000_images/ISIC_0025030.jpg  bkl   histo  80.0   
2  HAM_0002730  data/HAM10000_images/ISIC_0026769.jpg  bkl   histo  80.0   
3  HAM_0002730  data/HAM10000_images/ISIC_0025661.jpg  bkl   histo  80.0   
4  HAM_0001466  data/HAM10000_images/ISIC_0031633.jpg  bkl   histo  75.0   

    sex localization  dx_num  
0  male        scalp       2  
1  male        scalp       2  
2  male        scalp       2  
3  male        scalp       2  
4  male          ear       2

In [11]:
from sklearn.utils import shuffle
df_shuffled = shuffle(df)
df_shuffled.head()

lesion_id                               image_id     dx    dx_type  \
9973  HAM_0007008  data/HAM10000_images/ISIC_0030036.jpg  akiec      histo   
7483  HAM_0001870  data/HAM10000_images/ISIC_0033090.jpg     nv      histo   
2821  HAM_0004495  data/HAM10000_images/ISIC_0024743.jpg    bcc      histo   
6143  HAM_0005593  data/HAM10000_images/ISIC_0029658.jpg     nv  follow_up   
1119  HAM_0007225  data/HAM10000_images/ISIC_0031429.jpg     df      histo   

       age     sex     localization  dx_num  
9973  60.0    male             hand       4  
7483  70.0    male             back       0  
2821  65.0  female  lower extremity       3  
6143  45.0    male             back       0  
1119  75.0    male  lower extremity       6

In [30]:
# testing_df = df_shuffled[:200]
testing_df = df_shuffled

In [31]:
datagen = ImageDataGenerator(
    rescale=1.0/255.0,
    horizontal_flip = True,
    vertical_flip = True,
    rotation_range = 20,
    validation_split=0.2
)

In [40]:
# the different dataframes created with the ImageDatagenerator
train_df = datagen.flow_from_dataframe(
    testing_df,
    directory = '',
    x_col = 'image_id',
    y_col = 'dx_num',
    subset='training',
    class_mode='raw',
    target_size=(256, 256),
    # classes=['nv', 'mel', 'bkl', 'bcc', 'akiec', 'vasc', 'df']
)
val_df = datagen.flow_from_dataframe(
    testing_df,
    directory = '',
    x_col = 'image_id',
    y_col = 'dx_num',
    subset='validation',
    class_mode='raw',
    target_size=(256, 256),
    # classes=['nv', 'mel', 'bkl', 'bcc', 'akiec', 'vasc', 'df']
)

Found 8012 validated image filenames.
Found 2003 validated image filenames.


In [15]:
# validating it is correctly created
for x, y in train_df:
    print(x.shape)
    print(y.shape)
    break

for x, y in val_df:
    print(x.shape)
    print(y.shape)
    break

(32, 450, 600, 3)
(32,)
(32, 450, 600, 3)
(32,)


In [61]:
import tensorflow as tf
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense, Input, Concatenate, Maximum, Dropout, LeakyReLU
from tensorflow.keras.models import Model


class ClassWeightMult(tf.keras.layers.Layer):
    def __init__(self, class_weight):
        super().__init__()
        self.class_weight = class_weight

    def call(self, inputs):
        return inputs * self.class_weight

    def get_config(self):
        config = super().get_config()
        config.update({
            "class_weight": self.class_weight,
        })
        return config

In [62]:
# the model goes here (definitions)
# previous best model with class weights this time
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense, Dropout, MaxPooling2D, BatchNormalization
from tensorflow.keras.models import Model


def seq_model(out=7):
    # sequential attempt
    inp =  Input((256, 256, 3))
    x = BatchNormalization()(inp)
    
    x = Conv2D(64, kernel_size=5, activation='relu', kernel_initializer='glorot_normal')(x)
    x = Conv2D(64, kernel_size=5, activation='relu', kernel_initializer='glorot_normal')(x)
    x = MaxPooling2D(pool_size=(2,2))(x)

    x = Conv2D(64, kernel_size=3, activation='relu', kernel_initializer='glorot_normal')(x)
    x = Conv2D(64, kernel_size=3, activation='relu', kernel_initializer='glorot_normal')(x)
    x = MaxPooling2D(pool_size=(2,2))(x)
    x = Dropout(0.2)(x)

    x = Conv2D(64, kernel_size=3, activation='relu', kernel_initializer='glorot_normal')(x)
    x = Conv2D(64, kernel_size=3, activation='relu', kernel_initializer='glorot_normal')(x)
    x = MaxPooling2D(pool_size=(2,2))(x)
    
    x = Conv2D(64, kernel_size=3, activation='relu', kernel_initializer='glorot_normal')(x)
    x = Conv2D(64, kernel_size=3, activation='relu', kernel_initializer='glorot_normal')(x)
    x = MaxPooling2D(pool_size=(2,2))(x)
    x = Dropout(0.3)(x)

    x = Flatten()(x)
    x = Dense(1024, activation='relu')(x)
    x = Dense(256, activation='relu')(x)
    x = Dense(64, activation='relu')(x)
    x = Dense(out, activation='softmax')(x)
    out = ClassWeightMult(cw)(x)
    
    model = Model(inp, out)

    print(model.summary())
    return model

In [63]:
# other possible models created by me
# the model goes here (definitions)
# previous best model with class weights this time
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense, Dropout, MaxPooling2D, BatchNormalization
from tensorflow.keras.models import Model


def simple_seq_model(out=7):
    # sequential attempt
    inp =  Input((256, 256, 3))
    x = BatchNormalization()(inp)
    
    x = Conv2D(64, kernel_size=6, strides=(3,3), activation='relu', kernel_initializer='glorot_normal')(x)
    x = Conv2D(64, kernel_size=6, strides=(3,3), activation='relu', kernel_initializer='glorot_normal')(x)
    x = MaxPooling2D(pool_size=(2,2))(x)
    x = Dropout(0.5)(x)

    x = Conv2D(64, kernel_size=3, strides=(1,1), activation='relu', kernel_initializer='glorot_normal')(x)
    x = Conv2D(64, kernel_size=3, strides=(1,1), activation='relu', kernel_initializer='glorot_normal')(x)
    x = MaxPooling2D(pool_size=(2,2))(x)
    x = Dropout(0.5)(x)

    x = Flatten()(x)
    x = Dense(512, activation='relu')(x)
    x = Dense(128, activation='relu')(x)
    x = Dense(out, activation='softmax')(x)
    out = ClassWeightMult(cw)(x)
    
    model = Model(inp, out)

    print(model.summary())
    return model

In [150]:
# transfer learning
# models
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense, Dropout
from tensorflow.keras.applications.inception_v3 import InceptionV3
from tensorflow.keras.applications.resnet50 import ResNet50
from tensorflow.keras.applications.vgg16 import VGG16
from tensorflow.keras.models import Model


def inception_v3(freeze_layers=30, inp_t=None, apply_weights=True):
    model = InceptionV3(weights='imagenet', include_top=False)
    
    x = model.output
    x = GlobalAveragePooling2D()(x)
    x = Dense(512, activation='relu')(x)
    x = Dropout(0.5)(x)
    x = Dense(512, activation='relu')(x)
    x = Dropout(0.5)(x)
    out = Dense(7, activation='softmax')(x)
    out = ClassWeightMult(cw)(out)

    model_final = Model(model.input, out)
    for layer in model.layers[0:freeze_layers]:
        layer.trainable = False

    # print(model_final.summary())
    return model_final


def resnet50(freeze_layers=10):
    model = ResNet50(weights='imagenet',include_top=False)

    x = model.output
    x = GlobalAveragePooling2D()(x)
    x = Dense(512, activation='relu')(x)
    x = Dropout(0.5)(x)
    x = Dense(512, activation='relu')(x)
    x = Dropout(0.5)(x)
    out = Dense(7,activation='softmax')(x)
    out = ClassWeightMult(cw)(out)

    model_final = Model(model.input, out)
    for layer in model.layers[0:freeze_layers]:
        layer.trainable = False

    # print(model_final.summary())
    return model_final


def vgg16(freeze_layers=10):
    model = VGG16(weights='imagenet',include_top=False)

    x = model.output
    x = GlobalAveragePooling2D()(x)
    x = Dense(512, activation='relu')(x)
    x = Dropout(0.5)(x)
    x = Dense(512, activation='relu')(x)
    x = Dropout(0.5)(x)
    out = Dense(7,activation='softmax')(x)
    out = ClassWeightMult(cw)(out)

    model_final = Model(model.input, out)
    for layer in model.layers[0:freeze_layers]:
        layer.trainable = False

    # print(model_final.summary())
    return model_final

In [66]:
# initialize which model here
model = simple_seq_model()

Model: "model_9"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_14 (InputLayer)       [(None, 256, 256, 3)]     0         
                                                                 
 batch_normalization_199 (Ba  (None, 256, 256, 3)      12        
 tchNormalization)                                               
                                                                 
 conv2d_236 (Conv2D)         (None, 84, 84, 64)        6976      
                                                                 
 conv2d_237 (Conv2D)         (None, 27, 27, 64)        147520    
                                                                 
 max_pooling2d_31 (MaxPoolin  (None, 13, 13, 64)       0         
 g2D)                                                            
                                                                 
 dropout_21 (Dropout)        (None, 13, 13, 64)        0   

In [67]:
from tensorflow.keras.optimizers import Adam

optimizer = Adam(learning_rate=0.001)
model.compile(
    optimizer=optimizer,
    loss=tf.keras.losses.SparseCategoricalCrossentropy(),
    metrics=['accuracy']
)

In [68]:
# fitting the model
lr_reduction = tf.keras.callbacks.ReduceLROnPlateau(
    monitor='val_loss', factor=0.1, patience=4, verbose=1,
    mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.0000001
)

checkpoint = tf.keras.callbacks.ModelCheckpoint("model/ham10000_rayaq_best.h5", save_best_only=True)

callbacks = [
    lr_reduction,
    checkpoint
]

model.fit(
    train_df,
    validation_data=val_df,
    epochs=3,
    verbose=1,
    callbacks=callbacks
)

Epoch 1/3
251/251 [==============================] - 125s 495ms/step - loss: 1.0572 - accuracy: 0.6470 - val_loss: 1.7220 - val_accuracy: 0.4154 - lr: 0.0010
Epoch 2/3
251/251 [==============================] - 119s 476ms/step - loss: 0.9532 - accuracy: 0.6704 - val_loss: 1.0396 - val_accuracy: 0.6620 - lr: 0.0010
Epoch 3/3
251/251 [==============================] - 118s 470ms/step - loss: 0.9080 - accuracy: 0.6804 - val_loss: 0.9133 - val_accuracy: 0.6595 - lr: 0.0010


In [151]:
# initialize which model here
model = inception_v3()

In [152]:
from tensorflow.keras.optimizers import Adam

# loading weights
# model.load_weights('87%_acc_model/ham10000_inceptionV3_best.h5')

optimizer = Adam(learning_rate=0.001)
model.compile(
    optimizer=optimizer,
    loss=tf.keras.losses.SparseCategoricalCrossentropy(),
    metrics=['accuracy']
)

In [154]:
# fitting the model
lr_reduction = tf.keras.callbacks.ReduceLROnPlateau(
    monitor='val_loss', factor=0.1, patience=4, verbose=1,
    mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.0000001
)

checkpoint = tf.keras.callbacks.ModelCheckpoint("model/ham10000_inceptionV3_best.h5", save_best_only=True)

callbacks = [
    lr_reduction,
    checkpoint
]

model.fit(
    train_df,
    validation_data=val_df,
    epochs=15,
    verbose=1,
    callbacks=callbacks
)

Epoch 1/15
251/251 [==============================] - 137s 544ms/step - loss: 0.4485 - accuracy: 0.8451 - val_loss: 0.4533 - val_accuracy: 0.8397 - lr: 0.0010
Epoch 2/15
251/251 [==============================] - 136s 540ms/step - loss: 0.4226 - accuracy: 0.8577 - val_loss: 0.4545 - val_accuracy: 0.8387 - lr: 0.0010
Epoch 3/15
 22/251 [=>............................] - ETA: 1:39 - loss: 0.3740 - accuracy: 0.8509

KeyboardInterrupt: 

In [155]:
# initialize which model here
model = resnet50()

In [156]:
from tensorflow.keras.optimizers import Adam

optimizer = Adam(learning_rate=0.1)
model.compile(
    optimizer=optimizer,
    loss=tf.keras.losses.SparseCategoricalCrossentropy(),
    metrics=['accuracy']
)

In [158]:
# fitting the model
lr_reduction = tf.keras.callbacks.ReduceLROnPlateau(
    monitor='val_loss', factor=0.1, patience=4, verbose=1,
    mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.0000001
)

checkpoint = tf.keras.callbacks.ModelCheckpoint("model/ham10000_resnet50_best.h5", save_best_only=True)

callbacks = [
    lr_reduction,
    checkpoint
]

model.fit(
    train_df,
    validation_data=val_df,
    epochs=8,
    verbose=1,
    callbacks=callbacks
)

Epoch 1/8
251/251 [==============================] - 165s 654ms/step - loss: 4.8948 - accuracy: 0.6641 - val_loss: 4.5037 - val_accuracy: 0.6910 - lr: 0.1000
Epoch 2/8
251/251 [==============================] - 159s 632ms/step - loss: 4.8948 - accuracy: 0.6641 - val_loss: 4.5037 - val_accuracy: 0.6910 - lr: 0.1000
Epoch 3/8
104/251 [===========>..................] - ETA: 1:18 - loss: 4.7976 - accuracy: 0.6708

KeyboardInterrupt: 

In [159]:
# initialize which model here
model = vgg16()

In [160]:
from tensorflow.keras.optimizers import Adam

optimizer = Adam(learning_rate=0.001)
model.compile(
    optimizer=optimizer,
    loss=tf.keras.losses.SparseCategoricalCrossentropy(),
    metrics=['accuracy']
)

In [161]:
# fitting the model
lr_reduction = tf.keras.callbacks.ReduceLROnPlateau(
    monitor='val_loss', factor=0.1, patience=4, verbose=1,
    mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.0000001
)

checkpoint = tf.keras.callbacks.ModelCheckpoint("model/ham10000_vgg16_best.h5", save_best_only=True)

callbacks = [
    lr_reduction,
    checkpoint
]

model.fit(
    train_df,
    validation_data=val_df,
    epochs=3,
    verbose=1,
    callbacks=callbacks
)

Epoch 1/3
143/251 [================>.............] - ETA: 1:02 - loss: 4.8088 - accuracy: 0.6596

KeyboardInterrupt: 

In [145]:
# transfer learning - special models
# models
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense, Dropout, GlobalMaxPooling2D
from tensorflow.keras.applications.inception_v3 import InceptionV3
from tensorflow.keras.applications.resnet50 import ResNet50
from tensorflow.keras.applications.vgg16 import VGG16
from tensorflow.keras.models import Model


def special_inception_v3(freeze_layers=30, inp_t=None):
    model = InceptionV3(weights='imagenet', include_top=False, input_tensor=inp_t)
    
    x = model.output
    x = GlobalMaxPooling2D()(x)
    x = Dense(512, activation='relu')(x)
    x = Dense(512, activation='relu')(x)
    out = Dropout(0.5)(x)
    

    model_final = Model(model.input, out)
    for layer in model.layers[0:freeze_layers]:
        layer.trainable = False

    # print(model_final.summary())
    return model_final


def special_resnet50(freeze_layers=10, inp_t=None):
    model = ResNet50(weights='imagenet',include_top=False, input_tensor=inp_t)

    x = model.output
    x = GlobalMaxPooling2D()(x)
    x = Dense(512, activation='relu')(x)
    x = Dropout(0.5)(x)
    out = Dense(512, activation='relu')(x)

    model_final = Model(model.input, out)
    for layer in model.layers[0:freeze_layers]:
        layer.trainable = False

    # print(model_final.summary())
    return model_final


def special_vgg16(freeze_layers=10, inp_t=None):
    model = VGG16(weights='imagenet',include_top=False, input_tensor=inp_t)

    x = model.output
    x = GlobalMaxPooling2D()(x)
    x = Dense(512, activation='relu')(x)
    x = Dropout(0.5)(x)
    out = Dense(512, activation='relu')(x)

    model_final = Model(model.input, out)
    for layer in model.layers[0:freeze_layers]:
        layer.trainable = False

    # print(model_final.summary())
    return model_final

In [146]:
# multi-model classifier
# transfer learning
# models
from tensorflow.keras import layers 
from tensorflow.keras.models import Model


freeze_layers = -25
inp = layers.Input(shape=(256,256,3))

inception_v3_model = special_inception_v3(30, inp)
resnet50_model = special_resnet50(10, inp)
vgg_model = special_vgg16(10, inp)

x = layers.add([inception_v3_model.output, resnet50_model.output, vgg_model.output])
x = layers.Dense(512, activation='relu')(x)
x = layers.Dense(128, activation='relu')(x)
x = layers.Dropout(0.5)(x)
x = layers.Dense(7, activation='softmax')(x)
out = ClassWeightMult(cw)(x)

multi_model = Model(inp, out)
multi_model.summary()

Model: "model_95"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_56 (InputLayer)          [(None, 256, 256, 3  0           []                               
                                )]                                                                
                                                                                                  
 conv1_pad (ZeroPadding2D)      (None, 262, 262, 3)  0           ['input_56[0][0]']               
                                                                                                  
 conv1_conv (Conv2D)            (None, 128, 128, 64  9472        ['conv1_pad[0][0]']              
                                )                                                                 
                                                                                           

In [147]:
from tensorflow.keras.utils import plot_model

plot_model(
    multi_model,
    to_file="multi_model.png",
    show_shapes=True,
    show_layer_names=True,
)

In [148]:
from tensorflow.keras.optimizers import Adam

optimizer = Adam(learning_rate=0.001)
multi_model.compile(
    optimizer=optimizer,
    loss=tf.keras.losses.SparseCategoricalCrossentropy(),
    metrics=['accuracy']
)

In [149]:
# fitting the model
lr_reduction = tf.keras.callbacks.ReduceLROnPlateau(
    monitor='val_loss', factor=0.1, patience=4, verbose=1,
    mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.0000001
)

checkpoint = tf.keras.callbacks.ModelCheckpoint("model/ham10000_multi_model_best.h5", save_best_only=True)

callbacks = [
    lr_reduction,
    checkpoint
]

multi_model.fit(
    train_df,
    validation_data=val_df,
    epochs=3,
    verbose=1,
    callbacks=callbacks
)

Epoch 1/3
251/251 [==============================] - 441s 2s/step - loss: 4.9391 - accuracy: 0.6600 - val_loss: 4.5037 - val_accuracy: 0.6910 - lr: 0.0010
Epoch 2/3
  2/251 [..............................] - ETA: 6:28 - loss: 4.0988 - accuracy: 0.7188

KeyboardInterrupt: 